In [3]:
# general
import os
BASE_DIR = os.path.dirname(os.path.dirname(os.path.abspath('__file__')))

from pathlib import Path

import warnings

from IPython.core.display import display, HTML

# computation
import math
import numpy as np
import pandas as pd
import geoglows
import hydrostats.data as hd
import hydrostats.analyze as ha
from scipy import interpolate

# plotting
import matplotlib.pyplot as plt
%matplotlib inline
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import bokeh as bk
import bokeh.plotting as bp
from bokeh.models import tools as bmt, tickers
from bokeh.io import output_notebook, export_png

output_notebook()

Loading BokehJS ...

In [4]:
stations = [
    'Battambang', 'Chaktomuk', 'Kg._Thmar', 'Koh_Khel', 'Kompong_Cham', 'Kompong_Chen', 'Kompong_Kdei', 'Kompong_Thom',
    'Kratie', 'Lumphat', 'Neak_Luong', 'Phnom_Penh_Port', 'Prek_Kdam', 'Siempang', 'Sisophon', 'Stung_Treng', 'Voeun_Sai',
]

no_fit_stations = ['Phnom_Penh_Port', 'Prek_Kdam']

In [5]:
dfs = []

for station in stations:
    obs = pd.read_csv(f'{BASE_DIR}/mrc_observations/{station}.csv')
    obs['datetime'] = pd.to_datetime(obs['datetime'])
    obs = obs.set_index('datetime')

    pred = pd.read_csv(f'{BASE_DIR}/spt_predictions/{station}.csv')
    pred['datetime'] = pd.to_datetime(pred['datetime'])
    pred = pred.set_index('datetime')

    obs = obs.rename(columns={'discharge': 'observation'})
    pred = pred.rename(columns={'discharge': 'prediction'})
    df = pd.merge(obs, pred, how='inner', on='datetime')
    dfs.append({'station': station, 'df_obs': obs, 'df_pred': pred})
    

In [6]:
def correct_historical(simulated_data: pd.DataFrame, observed_data: pd.DataFrame, extrapolate: bool = False) -> pd.DataFrame:
    """
    Copied from GeoGlows Github repo
    Accepts a historically simulated flow timeseries and observed flow timeseries and attempts to correct biases in the
    simulation on a monthly basis.
    Args:
        simulated_data: A dataframe with a datetime index and a single column of streamflow values
        observed_data: A dataframe with a datetime index and a single column of streamflow values
    Returns:
        pandas DataFrame with a datetime index and a single column of streamflow values
    """
    # list of the unique months in the historical simulation. should always be 1->12 but just in case...
    unique_simulation_months = sorted(set(simulated_data.index.strftime('%m')))
    dates = []
    values = []

    for month in unique_simulation_months:
        # filter historic data to only be current month
        monthly_simulated = simulated_data[simulated_data.index.month == int(month)].dropna()
        to_prob = _flow_and_probability_mapper(monthly_simulated, to_probability=True, extrapolate=extrapolate)
        # filter the observations to current month
        monthly_observed = observed_data[observed_data.index.month == int(month)].dropna()
        to_flow = _flow_and_probability_mapper(monthly_observed, to_flow=True, extrapolate=extrapolate)

        dates += monthly_simulated.index.to_list()
        value = to_flow(to_prob(monthly_simulated.values))
        values += value.tolist()

    corrected = pd.DataFrame(data=values, index=dates, columns=['Corrected Simulated Streamflow'])
    corrected.sort_index(inplace=True)
    return corrected

In [7]:
def _flow_and_probability_mapper(monthly_data: pd.DataFrame, to_probability: bool = False,
                                 to_flow: bool = False, extrapolate: bool = False) -> interpolate.interp1d:
    """     Copied from GeoGlows Github repo
    """
    if not to_flow and not to_probability:
        raise ValueError('You need to specify either to_probability or to_flow as True')

    # get maximum value to bound histogram
    max_val = math.ceil(np.max(monthly_data.max()))
    min_val = math.floor(np.min(monthly_data.min()))
    if max_val == min_val:
        warnings.warn('The observational data has the same max and min value. You may get unanticipated results.')
        max_val += .1

    # determine number of histograms bins needed
    number_of_points = len(monthly_data.values)
    number_of_classes = math.ceil(1 + (3.322 * math.log10(number_of_points)))

    # specify the bin width for histogram (in m3/s)
    step_width = (max_val - min_val) / number_of_classes

    # specify histogram bins
    bins = np.arange(-np.min(step_width), max_val + 2 * np.min(step_width), np.min(step_width))
    if bins[0] == 0:
        bins = np.concatenate((-bins[1], bins))
    elif bins[0] > 0:
        bins = np.concatenate((-bins[0], bins))

    # make the histogram
    counts, bin_edges = np.histogram(monthly_data, bins=bins)

    # adjust the bins to be the center
    bin_edges = bin_edges[1:]

    # normalize the histograms
    counts = counts.astype(float) / monthly_data.size

    # calculate the cdfs
    cdf = np.cumsum(counts)

    # interpolated function to convert simulated streamflow to prob
    if to_probability:
        if extrapolate:
            return interpolate.interp1d(bin_edges, cdf, fill_value='extrapolate')
        return interpolate.interp1d(bin_edges, cdf)
    # interpolated function to convert simulated prob to observed streamflow
    elif to_flow:
        if extrapolate:
            return interpolate.interp1d(cdf, bin_edges, fill_value='extrapolate')
        return interpolate.interp1d(cdf, bin_edges)

In [12]:
Path(f'{BASE_DIR}/plot_exports/bcorr_base/').mkdir(parents=True, exist_ok=True)

for station in dfs:

    name = station['station']
    
    df_pred = station['df_pred']
    df_obs = station['df_obs']
#     bias_corrected = geoglows.bias.correct_historical(df_pred, df_obs)
    bias_corrected = correct_historical(df_pred, df_obs, extrapolate=True)

    station['df_bcorr'] = bias_corrected

    # figure
    title = f'{name}: Bias Correction'
    x_axis_label = 'Datetime (UTC)'
    y_axis_label = 'Discharge (m3/s)'

    # bokeh style
    TOOLS = 'pan,wheel_zoom,box_zoom,reset'
    hover_tool = bmt.HoverTool(
        tooltips=[
            ('date',      '$x{%F}'),
            ('discharge', '$y{0.00 a}'),
        ],
        formatters={
            '$x' : 'datetime',
        },
    )

#     TOOLTIPS = [
#         ('date',      '$x'),
#         ('discharge', '$y'),
#     ]
#     hover_tool = bmt.HoverTool(tooltips=TOOLTIPS)

    fig = bp.figure(title=title,
                    x_axis_label=x_axis_label,
                    y_axis_label=y_axis_label,
                    plot_height=300,
                    tools=TOOLS,
                   )
    fig.add_tools(hover_tool)
    fig.sizing_mode = 'scale_width'

#     fig.circle(datetime, observation, source=df, size=5)
    fig.line('datetime', 'prediction', source=df_pred, line_width=2, line_color='red', legend_label='prediction')
    fig.line('datetime', 'observation', source=df_obs, line_width=2, line_color='blue', legend_label='observation')
    fig.line('index', 'Corrected Simulated Streamflow', source=bias_corrected, line_width=2, line_color='green', legend_label='bias-corrected')

    fig.legend.location = 'top_left'
    fig.legend.click_policy = 'hide'

    try:
        bp.show(fig)
        export_png(fig, filename=f'{BASE_DIR}/plot_exports/bcorr_base/{name}.png')
    except Exception as e:
        print(f'station: {station} error')
        print(e)


#   # webgl for fast render
#     prediction = go.Scattergl(x=df_pred.index,
#                               y=df_pred.prediction,
#                               name=f'Prediction',
#                               mode='lines',
#                               line=dict(color='red'),
#                               showlegend=True,
#                              )

#     observation = go.Scattergl(x=df_obs.index,
#                                y=df_obs.observation,
#                                mode='lines+text',
#                                name = f'Observation',
#                                line=dict(color='blue'),
#                                showlegend=True,
#                               )
    
#     bcorr = go.Scattergl(x=bias_corrected.index,
#                          y=bias_corrected['Corrected Simulated Streamflow'],
#                          mode='lines+text',
#                          name = f'Bias-Corrected Prediction',
#                          line=dict(color='green'),
#                          showlegend=True,
#                         )


#     layout = go.Layout(title=title,
#                        xaxis=dict(title=x_axis_label),
#                        yaxis=dict(title=y_axis_label),
#                        showlegend=True)

#     fig = go.Figure(data=[observation, prediction, bcorr], layout=layout)

#     fig.write_image(f'{BASE_DIR}/plot_exports/bcorr_base/{name}.png')

#     fig.show()


/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in multiply



/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in multiply

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in multiply

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in mu

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in multiply



/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in multiply

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in multiply

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in mu

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in multiply

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in multiply



/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in multiply

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in multiply

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:623: RuntimeWarning:

divide by zero encountered in true_divide

/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/scipy/interpolate/interpolate.py:626: RuntimeWarning:

invalid value encountered in mu

ValueError: cannot convert float NaN to integer

In [12]:
# ['Mean Error', 'Root Mean Square Error', 'Normalized Root Mean Square Error - Mean', 'Mean Absolute Percentage Error',
# 'Nash-Sutcliffe Efficiency', 'Kling-Gupta Efficiency (2009)', 'Kling-Gupta Efficiency (2012)', 'Pearson Correlation Coefficient',
# 'Spearman Rank Correlation Coefficient', 'Spearman Rank Correlation Coefficient', 'Coefficient of Determination'
# ]

# NSE - baseline is the mean of the observationn
# if the NSE <= 0, the model is no better than using the observed mean as the predictor

# 

metrics = ['ME', 'RMSE', 'NRMSE (Mean)', 'MAPE', 'NSE', 'KGE (2009)', 'KGE (2012)', 'R (Pearson)', 'R (Spearman)', 'r2']

for idx, station in enumerate(dfs):

    print('------------------------------')
    name = station['station']
    print(f'Station: {name}')
    
    df_pred = station['df_pred']
    df_obs = station['df_obs']
    df_bcorr = station['df_bcorr']

    df_orig = hd.merge_data(sim_df=df_pred, obs_df=df_obs)
    df_bcorr = hd.merge_data(sim_df=df_bcorr, obs_df=df_obs)

    # # Merge Data
    metrics_orig_vs_pred = ha.make_table(merged_dataframe=df_orig, metrics=metrics)
    metrics_orig_vs_bcorr = ha.make_table(merged_dataframe=df_bcorr, metrics=metrics)

    metrics_orig_vs_bcorr = metrics_orig_vs_bcorr.rename(index={'Full Time Series': 'Corrected Full Time Series'})
    metrics_orig_vs_pred = metrics_orig_vs_pred.rename(index={'Full Time Series': 'Original Full Time Series'})

    # df_orig_vs_bcorr
    metrics_orig_vs_bcorr = metrics_orig_vs_bcorr.transpose()
    metrics_orig_vs_pred = metrics_orig_vs_pred.transpose()

    table_final = pd.merge(metrics_orig_vs_bcorr, metrics_orig_vs_pred, right_index=True, left_index=True)

    display(HTML(table_final.to_html()))
    
    scatter = go.Scattergl(x=df_orig.Simulated.values,
                           y=df_orig.Observed.values,
                           mode='markers',
                           name='original',
                           marker=dict(color='red')
                          )
    
    scatter2 = go.Scattergl(x=df_bcorr.Simulated.values,
                            y=df_bcorr.Observed.values,
                            mode='markers',
                            name='corrected',
                            marker=dict(color='blue')
                           )
    
    min_orig = min(min(df_orig.Simulated.values), min(df_orig.Observed.values))
    max_orig = max(max(df_orig.Simulated.values), max(df_orig.Observed.values))
    
#     min_bcorr = min(min(df_bcorr.Simulated.values), min(df_bcorr.Observed.values))
#     max_bcorr = max(max(df_bcorr.Simulated.values), max(df_bcorr.Observed.values))
    
    desired = go.Scattergl(x=[min_orig, max_orig],
                           y=[min_orig, max_orig],
                           mode='lines',
                           name='1:1 line',
                           line=dict(color='black')
                          )
    layout = go.Layout(title=f'Scatter Plot - {name} (Log Scale)',
                       xaxis=dict(title='Simulated', type='log'),
                       yaxis=dict(title='Observed', type='log'),
                       showlegend=True)

    fig = go.Figure(data=[scatter, scatter2, desired], layout=layout)

#     fig.show()
    

------------------------------
Station: Battambang


------------------------------
Station: Chaktomuk


/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/HydroErr/HydroErr.py:6272: UserWarning:

Row(s) [3760 3761 3762 3763] contained Inf or -Inf values and the row(s) have been removed (Rows are zero indexed).



------------------------------
Station: Kg._Thmar


------------------------------
Station: Koh_Khel


...

------------------------------
Station: Siempang


------------------------------
Station: Sisophon


/Users/biplovbhandari/miniconda3/envs/cbias/lib/python3.9/site-packages/HydroErr/HydroErr.py:6272: UserWarning:

Row(s) [  16   23   24 ... 4866 4874 4883] contained Inf or -Inf values and the row(s) have been removed (Rows are zero indexed).



------------------------------
Station: Stung_Treng


------------------------------
Station: Voeun_Sai
